In [1]:
from OpenAITools.JRCTTools import DfPostProcess, get_matched_df
from sentence_transformers import SentenceTransformer, util
import pandas as pd

/Users/satoc/miniforge3/envs/gradio/lib/python3.12/site-packages/sentence_transformers/cross_encoder/CrossEncoder.py:13: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  from tqdm.autonotebook import tqdm, trange


In [2]:
exclusive_words = ["triple negative", "double positive","Malignant","recurrent","IDH wild-type", "High-Grade", "Low-grade"]
csv_loc = '../ClinicalTrialCSV/JRCT20241215Cancer.csv'
df = pd.read_csv(csv_loc, index_col=0)
# モデルのロード
model = SentenceTransformer('pritamdeka/S-PubMedBert-MS-MARCO')


/Users/satoc/miniforge3/envs/gradio/lib/python3.12/site-packages/transformers/tokenization_utils_base.py:1617: FutureWarning: `clean_up_tokenization_spaces` was not set. It will be set to `True` by default. This behavior will be deprecated in transformers v4.45, and will be then set to `False` by default. For more details check this issue: https://github.com/huggingface/transformers/issues/31884
  warnings.warn(


In [4]:
#processed_df = DfPostProcess(exclusive_words, model, csv_loc=csv_loc)
processed_df = DfPostProcess(exclusive_words, model, dataframe=df)

In [4]:
processed_df.to_csv("../ClinicalTrialCSV/JRCT20241215CancerPost.csv")

In [16]:
def get_matched_df(basedf, query, model, threshold=0.5):
    # queryをベクトル化（テンソル化）しCPUへ移動
    query_vec = model.encode(query, convert_to_tensor=True).cpu()

    matched_indices = []
    for idx, target_vec_str in enumerate(basedf['TargetVec']):
        # CSVから読み込んだ時点でTargetVecはPythonリストを文字列化したものになっているため、
        # ここでliteral_evalでリストに戻します。
        if isinstance(target_vec_str, str):
            # target_vec_strは"[[...], [...]]"のようなリスト形式
            target_list = ast.literal_eval(target_vec_str)  # リストに変換
            target_vecs = torch.tensor(target_list)         # リストからTensorへ
        else:
            # 万が一既にTensorの場合はそのまま使用
            target_vecs = target_vec_str

        # 必要であればCPUへ移動（通常はすでにCPU上のはず）
        """if target_vecs[0].is_cuda:
            target_vecs = target_vecs.cpu()"""

        # コサイン類似度を計算
        cosine_scores = util.cos_sim(query_vec, target_vecs).squeeze()

        # thresholdを超えるスコアが1つでもあればマッチと判断
        if (cosine_scores >= threshold).any():
            matched_indices.append(idx)

    # 条件を満たした行を抽出
    matched_df = basedf.iloc[matched_indices]
    return matched_df

In [17]:
processed_df['TargetVec'][0]

[[-0.12602144479751587,
  -0.7141546607017517,
  -0.4860573410987854,
  -0.6787610650062561,
  -0.5019499659538269,
  -0.13430769741535187,
  -0.6577554941177368,
  0.6076976656913757,
  0.12889647483825684,
  0.46750736236572266,
  0.018368367105722427,
  0.43061959743499756,
  0.1905517727136612,
  -0.32873567938804626,
  -0.43094030022621155,
  -0.21434563398361206,
  0.07665695995092392,
  0.27581971883773804,
  0.5334398150444031,
  0.1360682100057602,
  0.42274555563926697,
  0.310781329870224,
  -0.09085263311862946,
  -0.13402250409126282,
  -0.7091479301452637,
  0.3295823633670807,
  -0.017893081530928612,
  0.14529234170913696,
  0.33790770173072815,
  -0.5387213230133057,
  0.1965356171131134,
  0.43226656317710876,
  0.08384066075086594,
  1.2179083824157715,
  -0.1406896710395813,
  -0.19285115599632263,
  0.2328663468360901,
  -0.2901802659034729,
  0.21684598922729492,
  0.08382049202919006,
  0.8460990190505981,
  -0.24980926513671875,
  0.25551164150238037,
  0.210331

In [18]:
get_matched_df(processed_df, "breast cancer", model, threshold=0.925)

JRCT ID       NCT No JapicCTI No  \
31   jRCT2061240081  NCT06393374         NaN   
32   jRCT2031240476  NCT06312176         NaN   
157  jRCT2052240059          NaN         NaN   
170  jRCT2031240096  NCT06380751         NaN   
209  jRCT2031230750  NCT06188559         NaN   
215  jRCT2031230723  NCT06112379         NaN   
224  jRCT2051230196  NCT06105632         NaN   
234  jRCT2031230677  NCT06206837         NaN   
240  jRCT2061230102  NCT06103864         NaN   
307  jRCT2061230074  NCT05952557         NaN   
342  jRCT2051230094  NCT05794906         NaN   
351  jRCT2031230279  NCT05862285         NaN   
385  jRCT2031230121  NCT04557449         NaN   
388  jRCT2031230109  NCT05514054         NaN   
391  jRCT2031230090          NaN         NaN   
392  jRCT2031230096  NCT05774951         NaN   
402  jRCT2061230009  NCT05485766         NaN   
463  jRCT2061220087  NCT05629585         NaN   
515  jRCT2031220276  NCT05307705         NaN   
555  jRCT2031220034  NCT04862663         NaN   
590  jRCT2031210585  NCT05123482         NaN   
593  jRCT2031210560  NCT05061823         NaN   
600  jRCT2041210123  NCT05114746         NaN   
629  jRCT2052210099          NaN         NaN   
691  jRCT2031200384  NCT04221542         NaN   
698  jRCT2071200086  NCT04640623         NaN   
729  jRCT2031200057          NaN         NaN   

                                                 Title  \
31   術前薬物療法後の手術時に病理学的完全奏効を達成していないトリプルネガティブ乳癌患者を対象に、...   
32   ホルモン受容体陽性・ヒト上皮成長因子受容体2陰性（HR+/HER2-）の切除不能な局所進行又...   
157  遺伝子HSD17B4高メチル化を有するHER2陽性ER陰性乳癌における非手術療法の有用性を評...   
170  本治験の主要目的は、BRCA1、BRCA2 又は PALB2 変異を有し、HR 陽性、HER...   
209  治療歴のある HER2 陽性又は HER2 低発現の切除不能又は転移性乳癌の被験者を対象に，...   
215  未治療のトリプルネガティブ又はホルモン受容体低発現／HER2陰性乳癌の成人患者を対象として、...   
224  CDK4/6 阻害薬による前治療で進行したホルモン受容体陽性HER2 陰性の進行または転移乳...   
234  18歳以上のER陽性／HER2陰性の進行または転移乳癌患者を対象として，経口タンパク質分解誘...   
240  Programmed death-ligand（PD-L1）陽性の局所再発手術不能又は転移性...   
307  根治的局所治療（化学療法の併用または非併用）を受けて疾患の兆候のない、再発リスクが中間～高リ...   
342  前立腺癌の高リスク生化学的再発（BCR）患者を対象としたアンドロゲン遮断療法（ADT）を併用...   
351  GENENTECH社及び／又はF.HOFFMANN-LA ROCHE LTDが依頼した試験に...   
385  進行固形がん患者を対象として，PF-07220060 の単剤投与および併用投与の安全性，忍容...   
388  EMBER-4：2～5年間の術後内分泌療法による前治療歴を有する再発高リスクのER+、HER...   
391  MELK阻害剤OTS167POにおける転移性・進行性乳がん患者を対象とした安全性、忍容性およ...   
392  根治的局所領域療法（化学療法の併用または非併用）および標準補助内分泌療法（ET）を少なくとも...   
402  gBRCA1/2遺伝子変異を有するトリプルネガティブ原発乳がんに対するプラチナ製剤、PARP...   
463  術前薬物療法後の外科的切除時に乳房及び／又は腋窩リンパ節に浸潤性残存病変を有するステージI～...   
515  PIK3CA H1047R変異を有する進行乳がん患者及びその他の固形がん患者を対象としたLO...   
555  局所進行（切除不能）又は転移性のホルモン受容体陽性／ヒト上皮細胞成長因子受容体2 陰性乳癌を...   
590  進行又は転移性固形がん患者を対象としたAZD8205の単独療法及び他の抗がん剤との併用療法に...   
593  複数のBintrafusp alfa（M7824）臨床試験の被験者を対象に長期データを収集す...   
600  進行性PSMA陽性転移性去勢抵抗性前立腺がん（mCRPC）を有する患者を対象に177Lu-P...   
629  乳がんを有する成人女性及び健康成人女性を対象とした乳房用マイクロ波画像診断装置IGS-000...   
691  転移性去勢抵抗性前立腺がん患者を対象としたAMG 509の安全性、忍容性、薬物動態及び有効性...   
698  膀胱全摘除術に不適格である，又は膀胱全摘除術を選択しなかった，カルメット・ゲラン桿菌（BCG...   
729      治療抵抗性乳がんを対象としたTDM-812の腫瘍内投与法の安全性評価を目的とした第I相試験   

                                         TargetJ  \
31                                   トリプルネガティブ乳癌   
32                  HR+/HER2-の切除不能局所進行又は転移性乳癌の患者   
157                                          乳がん   
170                                         進行乳癌   
209               HER2 陽性又は HER2 低発現の切除不能又は転移性乳癌   
215                                           乳癌   
224  ホルモン受容体（HR）陽性ヒト上皮増殖因子受容体2（HER2）陰性の進行または転移乳癌   
234       エストロゲン受容体陽性／ヒト上皮増殖因子受容体 2 陰性の進行または転移乳癌   
240                                           乳癌   
307                                    乳がん、早期乳がん   
342                                         前立腺癌   
351                                            癌   
385                  進行または転移性の乳癌，前立腺癌，およびその他の固形癌   
388                                           乳癌   
391            再発・難治性の局所進行性・転移性乳がん及びトリプルネガティブ乳がん   
392                                    乳がん、早期乳がん   
402                                 トリプルネガティブ乳がん   
463                                           乳癌   
515                                          乳がん   
55

In [19]:
get_matched_df(processed_df, "glioma", model, threshold=0.92)

JRCT ID       NCT No JapicCTI No  \
82   jRCT2051240121  NCT06413706         NaN   
87   jRCT2051240119  NCT03423628         NaN   
175  jRCT2031240090          NaN         NaN   
263  jRCT2041230136          NaN         NaN   
361  jRCT2051230069          NaN         NaN   
401  jRCT2032230060          NaN         NaN   
414  jRCT2031230007          NaN         NaN   
636  jRCT2031210299          NaN         NaN   
712  jRCT2031200153          NaN         NaN   

                                                 Title  \
82   放射線療法後の悪性神経膠腫の小児および若年成人を対象に、アベマシクリブ＋テモゾロミドとテモゾ...   
87   多形性膠芽腫患者及び固形がんの脳転移患者を対象に、放射線療法併用下でAZD1390を漸増投与...   
175  再発悪性神経膠腫に対する治療用放射性薬剤64Cu-ATSMの有効性を検証するランダム化比較医...   
263                   再発膠芽腫に対するTUG1を標的とした核酸医薬医師主導第I相試験   
361  神経膠腫患者に対するロムスチン療法とプロカルバジン、ロムスチン、ビンクリスチン併⽤療法の安全...   
401  初発IDH野生型低悪性度神経膠腫に対する交流電場腫瘍治療システムの有効性と安全性を検証する多...   
414  BRAF融合遺伝子陽性の進行・再発の低悪性度神経膠腫または膵癌に対するビニメチニブの第Ⅱ相医...   
636                     再発悪性神経膠腫患者を対象としたDSP-0390の第1相試験   
712                     Cellm-001による初発膠芽腫治療効果無作為比較対照試験   

                         TargetJ                         Target  \
82                        悪性神経膠腫                         悪性神経膠腫   
87                      再発多形性膠芽腫                       再発多形性膠芽腫   
175                       悪性神経膠腫                         悪性神経膠腫   
263                        再発膠芽腫                          再発膠芽腫   
361                         神経膠腫                           神経膠腫   
401  IDH野生型神経膠腫（グレードⅢ）（退形成性星細胞腫）  IDH野生型神経膠腫(グレードIII)(退形成性星細胞腫)   
414                  低悪性度神経膠腫、膵癌                    低悪性度神経膠腫、膵癌   
636                     再発悪性神経膠腫                       再発悪性神経膠腫   
712                          膠芽腫                            膠芽腫   

                                         TargetEnglish  \
82                                   High-Grade Glioma   
87                   Recurrent Glioblastoma Multiforme   
175                                   Malignant glioma   
263                             recurrent glioblastoma   
361                                             Glioma   
401  IDH wild-type glioma (grade III) (anaplastic a...   
414                Low-grade glioma, pancreatic cancer   
636                        Recurrent High-Grade Glioma   
712                                       glioblastoma   

                                              研究・治験の目的 試験等のフェーズ 試験の種類  ...  \
82   放射線療法後の悪性神経膠腫を有する小児および若年成人を対象に、アベマシクリブとテモゾロミドの...        2   NaN  ...   
87                                           Treatment        1   NaN  ...   
175  再発・難治性悪性神経膠腫を対象として、64Cu-diacetyl-bis(N4-methyl...        3   NaN  ...   
263  再発膠芽腫患者を対象としてTUG1ASOを投与した場合の投与時の安全性を検討し、至適投与量を...        1   NaN  ...   
361  神経膠腫患者におけるロムスチン療法とプロカルバジン、ロムスチン、ビンクリスチン併用療法の安全...        1   NaN  ...   
401  初発IDH野生型低悪性度神経膠腫を対象に、放射線化学療法後のテモゾロミド維持療法期における交...        2   NaN  ...   
414  BRAF融合遺伝子または遺伝子再構成陽性の切除不能または再発の低悪性度神経膠腫(コホート A...        2   NaN  ...   
636  再発悪性神経膠腫患者を対象にDSP-0390を経口投与したときの安全性、薬物動態、薬力学及び...        1   NaN  ...   
712  脳腫瘍のうち、初発悪性膠芽腫に対する自家脳腫瘍免疫賦活剤であるCellm-001について、術...        3   NaN  ...   

                                    Inclusion Criteria  \
82   Subjects required to meet all the folloiwng cr...   
87   - Provision of formalin-fixed paraffin embedde...   
175  1) Histologically diagnosed as high grade glio...   
263  (1) Patients with a histological diagnosis of ...   
361  <Cohort 1> All of the following items shall be...   
401  At the time of enrollment, patients will be in...   
414  Inclusion criteria for both cohort A and B 1) ...   
636  1. Estimated life expectancy >= 3 months 2. Re...   
712  (1) 18 years old or older and 75 years old or ...   

                                    Exclusion Criteria     Age Minimum  \
82   Patients who meets any of the following criter...        No limit   
87   - Administration of chemotherapy or any invest...  18age old over   
175  1) Have a history or merger of other malignanc...  18age old over   
263  (1) Patients with extracerebral met

In [28]:
get_matched_df(processed_df, "glioma", model, threshold=0.9)

JRCT ID       NCT No JapicCTI No  \
82   jRCT2051240121  NCT06413706         NaN   
87   jRCT2051240119  NCT03423628         NaN   
175  jRCT2031240090          NaN         NaN   
263  jRCT2041230136          NaN         NaN   
272  jRCT2032230554          NaN         NaN   
361  jRCT2051230069          NaN         NaN   
401  jRCT2032230060          NaN         NaN   
414  jRCT2031230007          NaN         NaN   
636  jRCT2031210299          NaN         NaN   
712  jRCT2031200153          NaN         NaN   

                                                 Title  \
82   放射線療法後の悪性神経膠腫の小児および若年成人を対象に、アベマシクリブ＋テモゾロミドとテモゾ...   
87   多形性膠芽腫患者及び固形がんの脳転移患者を対象に、放射線療法併用下でAZD1390を漸増投与...   
175  再発悪性神経膠腫に対する治療用放射性薬剤64Cu-ATSMの有効性を検証するランダム化比較医...   
263                   再発膠芽腫に対するTUG1を標的とした核酸医薬医師主導第I相試験   
272  初発膠芽腫に対する新型高出力中性子線源を用いた加速器BNCT装置iBNCT001及びSPM-...   
361  神経膠腫患者に対するロムスチン療法とプロカルバジン、ロムスチン、ビンクリスチン併⽤療法の安全...   
401  初発IDH野生型低悪性度神経膠腫に対する交流電場腫瘍治療システムの有効性と安全性を検証する多...   
414  BRAF融合遺伝子陽性の進行・再発の低悪性度神経膠腫または膵癌に対するビニメチニブの第Ⅱ相医...   
636                     再発悪性神経膠腫患者を対象としたDSP-0390の第1相試験   
712                     Cellm-001による初発膠芽腫治療効果無作為比較対照試験   

                         TargetJ                         Target  \
82                        悪性神経膠腫                         悪性神経膠腫   
87                      再発多形性膠芽腫                       再発多形性膠芽腫   
175                       悪性神経膠腫                         悪性神経膠腫   
263                        再発膠芽腫                          再発膠芽腫   
272                        初発膠芽腫                          初発膠芽腫   
361                         神経膠腫                           神経膠腫   
401  IDH野生型神経膠腫（グレードⅢ）（退形成性星細胞腫）  IDH野生型神経膠腫(グレードIII)(退形成性星細胞腫)   
414                  低悪性度神経膠腫、膵癌                    低悪性度神経膠腫、膵癌   
636                     再発悪性神経膠腫                       再発悪性神経膠腫   
712                          膠芽腫                            膠芽腫   

                                         TargetEnglish  \
82                                   High-Grade Glioma   
87                   Recurrent Glioblastoma Multiforme   
175                                   Malignant glioma   
263                             recurrent glioblastoma   
272                       Newly-diagnosed glioblastoma   
361                                             Glioma   
401  IDH wild-type glioma (grade III) (anaplastic a...   
414                Low-grade glioma, pancreatic cancer   
636                        Recurrent High-Grade Glioma   
712                                       glioblastoma   

                                              研究・治験の目的 試験等のフェーズ 試験の種類  ...  \
82   放射線療法後の悪性神経膠腫を有する小児および若年成人を対象に、アベマシクリブとテモゾロミドの...        2   NaN  ...   
87                                           Treatment        1   NaN  ...   
175  再発・難治性悪性神経膠腫を対象として、64Cu-diacetyl-bis(N4-methyl...        3   NaN  ...   
263  再発膠芽腫患者を対象としてTUG1ASOを投与した場合の投与時の安全性を検討し、至適投与量を...        1   NaN  ...   
272  治験機器iBNCT001及び治験薬SPM-011を用いたホウ素中性子捕捉療法(BNCT)に、...        1   NaN  ...   
361  神経膠腫患者におけるロムスチン療法とプロカルバジン、ロムスチン、ビンクリスチン併用療法の安全...        1   NaN  ...   
401  初発IDH野生型低悪性度神経膠腫を対象に、放射線化学療法後のテモゾロミド維持療法期における交...        2   NaN  ...   
414  BRAF融合遺伝子または遺伝子再構成陽性の切除不能または再発の低悪性度神経膠腫(コホート A...        2   NaN  ...   
636  再発悪性神経膠腫患者を対象にDSP-0390を経口投与したときの安全性、薬物動態、薬力学及び...        1   NaN  ...   
712  脳腫瘍のうち、初発悪性膠芽腫に対する自家脳腫瘍免疫賦活剤であるCellm-001について、術...        3   NaN  ...   

                                    Inclusion Criteria  \
82   Subjects required to meet all the folloiwng cr...   
87   - Provision of formalin-fixed paraffin embedde...   
175  1) Histologically diagnosed as high grade glio...   
263  (1) Patients with a histological diagnosis of ...   
272  - Karnofsky Performance Status is greater than...   
361  <Cohort 1> All of the following items shall be...   
401  At the time of enrollment, patients will be in...   
414  Inclusion criteria for both cohort A and B 1) ...   
636  1. Estimated life expectancy >= 3 months 2. Re...   
712  (1) 18 years old or old